In [2]:
import torch
from transformers import BertTokenizer
from IPython.display import clear_output

PRETRAINED_MODEL_NAME = "bert-base-chinese"  # 指定繁簡中文 BERT-BASE 預訓練模型

# 取得此預訓練模型所使用的 tokenizer
tokenizer = BertTokenizer.from_pretrained(PRETRAINED_MODEL_NAME)

clear_output()
print("PyTorch 版本：", torch.__version__)

PyTorch 版本： 1.2.0+cu92


In [12]:
# print (torch.cuda.current_device())
# print (torch.cuda.device_count()) # 返回当前可见可用的 GPU 数量
# print (torch.cuda.get_device_name()) # 获取 GPU 名称

import torch.nn as nn
from transformers import BertForSequenceClassification

PRETRAINED_MODEL_NAME = "bert-base-chinese"
NUM_LABELS = 2

model = BertForSequenceClassification.from_pretrained(
    PRETRAINED_MODEL_NAME, num_labels=NUM_LABELS)

clear_output()

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu") # 單GPU或者CPU
# model.to(device)
#如果是多GPU
if torch.cuda.device_count() > 1:
    # model = nn.DataParallel(model，device_ids=[0,1,2])
    model = nn.DataParallel(model, device_ids=[0,1,2])
# model.to(device)
print (torch.cuda.current_device())

/usr/local/lib/python3.6/dist-packages/torch/nn/parallel/data_parallel.py:26: UserWarning: 
    There is an imbalance between your GPUs. You may want to exclude GPU 2 which
    has less than 75% of the memory or cores of GPU 1. You can do so by setting
    the device_ids argument to DataParallel, or by setting the CUDA_VISIBLE_DEVICES
    environment variable.
  warnings.warn(imbalance_warn.format(device_ids[min_pos], device_ids[max_pos]))


0


In [ ]:

net = torch.nn.DataParallel(model, device_ids=[0, 1, 2])
output = net(input_var)  # input_var can be on any device, including CPU

In [2]:
import pandas as pd
from torch.utils.data import Dataset
 
    
class FakeNewsDataset(Dataset):
    # 讀取前處理後的 tsv 檔並初始化一些參數
    def __init__(self, mode, tokenizer):
        assert mode in ["train", "test"]  # 一般訓練你會需要 dev set
        self.mode = mode
        # 大數據你會需要用 iterator=True
        self.df = pd.read_csv(mode + ".tsv", sep="\t").fillna("")
        self.len = len(self.df)
        self.label_map = {'unlike': 0, 'like': 1}
        print (self.df.label.value_counts() / len(self.df))
        self.tokenizer = tokenizer  # 我們將使用 BERT tokenizer
    
    # 定義回傳一筆訓練 / 測試數據的函式
    def __getitem__(self, idx):
        if self.mode == "test":
            text_a, text_b = self.df.iloc[idx, :2].values
            label_tensor = None
        else:
            text_a, text_b, label = self.df.iloc[idx, :].values
            # 將 label 文字也轉換成索引方便轉換成 tensor
            label_id = self.label_map[label]
            label_tensor = torch.tensor(label_id)
            
        # 建立第一個句子的 BERT tokens 並加入分隔符號 [SEP]
        word_pieces = ["[CLS]"]
        tokens_a = self.tokenizer.tokenize(text_a)
        word_pieces += tokens_a + ["[SEP]"]
        len_a = len(word_pieces)
        
        # 第二個句子的 BERT tokens
        tokens_b = self.tokenizer.tokenize(text_b)
        word_pieces += tokens_b + ["[SEP]"]
        len_b = len(word_pieces) - len_a
        
        # 將整個 token 序列轉換成索引序列
        ids = self.tokenizer.convert_tokens_to_ids(word_pieces)
        tokens_tensor = torch.tensor(ids)
        
        # 將第一句包含 [SEP] 的 token 位置設為 0，其他為 1 表示第二句
        segments_tensor = torch.tensor([0] * len_a + [1] * len_b, 
                                        dtype=torch.long)
        
        return (tokens_tensor, segments_tensor, label_tensor)
    
    def __len__(self):
        return self.len
    
    
# 初始化一個專門讀取訓練樣本的 Dataset，使用中文 BERT 斷詞
trainset = FakeNewsDataset("train", tokenizer=tokenizer)

unlike    0.99237
like      0.00763
Name: label, dtype: float64


In [3]:
# 選擇第一個樣本
sample_idx = 0

# 將原始文本拿出做比較
text_a, text_b, label = trainset.df.iloc[sample_idx].values

# 利用剛剛建立的 Dataset 取出轉換後的 id tensors
tokens_tensor, segments_tensor, label_tensor = trainset[sample_idx]

# 將 tokens_tensor 還原成文本
tokens = tokenizer.convert_ids_to_tokens(tokens_tensor.tolist())
combined_text = "".join(tokens)

# 渲染前後差異，毫無反應就是個 print。可以直接看輸出結果
print(f"""[原始文本]
句子 1：{text_a}
句子 2：{text_b}
分類  ：{label}

--------------------

[Dataset 回傳的 tensors]
tokens_tensor  ：{tokens_tensor}

segments_tensor：{segments_tensor}

label_tensor   ：{label_tensor}

--------------------

[還原 tokens_tensors]
{combined_text}
""")

[原始文本]
句子 1：香蕉所表示近日低溫細雨香蕉葉部病害易發生，防檢局籲請農友加強注意病徵，以及時進行防治

句子 2：二期作水稻已陸續完成插秧，請留意防治水稻水象鼻蟲

分類  ：unlike

--------------------

[Dataset 回傳的 tensors]
tokens_tensor  ：tensor([ 101, 7676, 5933, 2792, 6134, 4850, 6818, 3189,  856, 3984, 5169, 7433,
        7676, 5933, 5864, 6956, 4567, 2154, 3211, 4634, 4495, 8024, 7344, 3596,
        2229, 5100, 6313, 6803, 1351, 1217, 2485, 3800, 2692, 4567, 2547, 8024,
         809, 1350, 3229, 6868, 6121, 7344, 3780,  102,  753, 3309,  868, 3717,
        4940, 2347, 7380, 5265, 2130, 2768, 2991, 4913, 8024, 6313, 4522, 2692,
        7344, 3780, 3717, 4940, 3717, 6496, 7965, 6100,  102])

segments_tensor：tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

label_tensor   ：0

--------------------

[還原 tokens_tensors]
[CLS]香蕉所表示近日低溫細雨香蕉葉部病害易發生，防檢局籲請農友加強注意病徵，以及時進行防治[SEP]二期作水稻已陸續完成插秧，請

In [4]:
"""
實作可以一次回傳一個 mini-batch 的 DataLoader
這個 DataLoader 吃我們上面定義的 `FakeNewsDataset`，
回傳訓練 BERT 時會需要的 4 個 tensors：
- tokens_tensors  : (batch_size, max_seq_len_in_batch)
- segments_tensors: (batch_size, max_seq_len_in_batch)
- masks_tensors   : (batch_size, max_seq_len_in_batch)
- label_ids       : (batch_size)
"""

from torch.utils.data import DataLoader
from torch.nn.utils.rnn import pad_sequence

# 這個函式的輸入 `samples` 是一個 list，裡頭的每個 element 都是
# 剛剛定義的 `FakeNewsDataset` 回傳的一個樣本，每個樣本都包含 3 tensors：
# - tokens_tensor
# - segments_tensor
# - label_tensor
# 它會對前兩個 tensors 作 zero padding，並產生前面說明過的 masks_tensors


def create_mini_batch(samples):
    tokens_tensors = [s[0] for s in samples]
    segments_tensors = [s[1] for s in samples]
    # 測試集有 labels
    if samples[0][2] is not None:
        label_ids = torch.stack([s[2] for s in samples])
    else:
        label_ids = None
    
    # zero pad 到同一序列長度
    tokens_tensors = pad_sequence(tokens_tensors, 
                                  batch_first=True)
    segments_tensors = pad_sequence(segments_tensors, 
                                    batch_first=True)
    
    # attention masks，將 tokens_tensors 裡頭不為 zero padding
    # 的位置設為 1 讓 BERT 只關注這些位置的 tokens
    masks_tensors = torch.zeros(tokens_tensors.shape, 
                                dtype=torch.long)
    masks_tensors = masks_tensors.masked_fill(
        tokens_tensors != 0, 1)
    
    return tokens_tensors, segments_tensors, masks_tensors, label_ids


# 初始化一個每次回傳 64 個訓練樣本的 DataLoader
# 利用 `collate_fn` 將 list of samples 合併成一個 mini-batch 是關鍵
BATCH_SIZE = 4
trainloader = DataLoader(trainset, batch_size=BATCH_SIZE, 
                         collate_fn=create_mini_batch)

In [5]:
data = next(iter(trainloader))

tokens_tensors, segments_tensors, \
    masks_tensors, label_ids = data

print(f"""
tokens_tensors.shape   = {tokens_tensors.shape} 
{tokens_tensors}
------------------------
segments_tensors.shape = {segments_tensors.shape}
{segments_tensors}
------------------------
masks_tensors.shape    = {masks_tensors.shape}
{masks_tensors}
------------------------
label_ids.shape        = {label_ids.shape}
{label_ids}
""")


tokens_tensors.shape   = torch.Size([4, 104]) 
tensor([[ 101, 7676, 5933, 2792, 6134, 4850, 6818, 3189,  856, 3984, 5169, 7433,
         7676, 5933, 5864, 6956, 4567, 2154, 3211, 4634, 4495, 8024, 7344, 3596,
         2229, 5100, 6313, 6803, 1351, 1217, 2485, 3800, 2692, 4567, 2547, 8024,
          809, 1350, 3229, 6868, 6121, 7344, 3780,  102,  753, 3309,  868, 3717,
         4940, 2347, 7380, 5265, 2130, 2768, 2991, 4913, 8024, 6313, 4522, 2692,
         7344, 3780, 3717, 4940, 3717, 6496, 7965, 6100,  102,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0],
        [ 101, 7676, 5933, 2792, 6134, 4850, 6818, 3189,  856, 3984, 5169, 7433,
         7676, 5933, 5864, 6956, 4567, 2154, 3211, 4634, 4495, 8024, 7344, 3596,
         2229, 5100, 6313, 6803, 1351, 1217, 2485, 3800, 2692, 4567, 2547, 8024,
   

In [7]:
# 載入一個可以做中文多分類任務的模型，n_class = 3
from transformers import BertForSequenceClassification

PRETRAINED_MODEL_NAME = "bert-base-chinese"
NUM_LABELS = 2

model = BertForSequenceClassification.from_pretrained(
    PRETRAINED_MODEL_NAME, num_labels=NUM_LABELS)

clear_output()

# high-level 顯示此模型裡的 modules
print("""
name            module
----------------------""")
for name, module in model.named_children():
    if name == "bert":
        for n, _ in module.named_children():
            print(f"{name}:{n}")
    else:
        print("{:15} {}".format(name, module))


name            module
----------------------
bert:embeddings
bert:encoder
bert:pooler
dropout         Dropout(p=0.1, inplace=False)
classifier      Linear(in_features=768, out_features=2, bias=True)


## class BertForSequenceClassification(BertPreTrainedModel):
    def __init__(self, config, num_labels=2, ...):
        super(BertForSequenceClassification, self).__init__(config)
        self.num_labels = num_labels
        self.bert = BertModel(config, ...)  # 載入預訓練 BERT
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        # 簡單 linear 層
        self.classifier = nn.Linear(config.hidden_size, num_labels)
          ...

    def forward(self, input_ids, token_type_ids=None, attention_mask=None, labels=None, ...):
        # BERT 輸入就是 tokens, segments, masks
        outputs = self.bert(input_ids, token_type_ids, attention_mask, ...)
        ...
        pooled_output = self.dropout(pooled_output)
        # 線性分類器將 dropout 後的 BERT repr. 轉成類別 logits
        logits = self.classifier(pooled_output)

        # 輸入有 labels 的話直接計算 Cross Entropy 回傳，方便！
        if labels is not None:
            loss_fct = CrossEntropyLoss()
            loss = loss_fct(logits.view(-1, self.num_labels), labels.view(-1))
            return loss
        # 有要求回傳注意矩陣的話回傳
        elif self.output_attentions:
            return all_attentions, logits
        # 回傳各類別的 logits
        return logits

In [ ]:
model.config

In [8]:
"""
定義一個可以針對特定 DataLoader 取得模型預測結果以及分類準確度的函式
之後也可以用來生成上傳到 Kaggle 競賽的預測結果

在將 `tokens`、`segments_tensors` 等 tensors
丟入模型時，強力建議指定每個 tensor 對應的參數名稱，以避免 HuggingFace
更新 repo 程式碼並改變參數順序時影響到我們的結果。
"""
import os

# os.environ["CUDA-VISIBLE-DEVICES"] = '3'
# torch.cuda.set_device(2) # 這行加了也能跑


def get_predictions(model, dataloader, compute_acc=False):
    predictions = None
    correct = 0
    total = 0
    jindu = 0
      
    with torch.no_grad():
        # 遍巡整個資料集
        for data in dataloader:
            # 將所有 tensors 移到 GPU 上
            if next(model.parameters()).is_cuda:
                data = [t.to("cuda:0") for t in data if t is not None]
            
            
            # 別忘記前 3 個 tensors 分別為 tokens, segments 以及 masks
            # 且強烈建議在將這些 tensors 丟入 `model` 時指定對應的參數名稱
            tokens_tensors, segments_tensors, masks_tensors = data[:3]
            outputs = model(input_ids=tokens_tensors, 
                            token_type_ids=segments_tensors, 
                            attention_mask=masks_tensors)
            
            logits = outputs[0]
            _, pred = torch.max(logits.data, 1)
            
            # 用來計算訓練集的分類準確率
            if compute_acc:
                labels = data[3]
                total += labels.size(0)
                correct += (pred == labels).sum().item()
                
            # 將當前 batch 記錄下來
            if predictions is None:
                predictions = pred
            else:
                predictions = torch.cat((predictions, pred))
            
            jindu += BATCH_SIZE
            print(jindu)
    
    if compute_acc:
        acc = correct / total
        print(acc)
        return predictions, acc
    return predictions
    
# 讓模型跑在 GPU 上並取得訓練集的分類準確率
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print("device:", device)
model = model.to(device)
test, acc = get_predictions(model, trainloader, compute_acc=True)
print("classification acc:", acc)

device: cuda:0
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


...

True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


In [9]:
import pickle


pickle.dump(model, open('model.pkl', 'wb'))
# model = pickle.load(open('model.pkl', 'rb'))


In [10]:
def get_learnable_params(module):
    return [p for p in module.parameters() if p.requires_grad]
     
model_params = get_learnable_params(model)
clf_params = get_learnable_params(model.classifier)

print(f"""
整個分類模型的參數量：{sum(p.numel() for p in model_params)}
線性分類器的參數量：{sum(p.numel() for p in clf_params)}
""")


整個分類模型的參數量：102269186
線性分類器的參數量：1538



In [ ]:
%%time

device = torch.device("cuda:0,1" if torch.cuda.is_available() else "cpu") ## specify the GPU id's, GPU id's start from 0.
model = pickle.load(open('model.pkl', 'rb'))
# model= nn.DataParallel(model,device_ids = [0, 1])
model.to(device)

# torch.cuda.set_device(2)
# device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

! nvidia-smi

# 訓練模式
model.train()

# 使用 Adam Optim 更新整個分類模型的參數
optimizer = torch.optim.Adam(model.parameters(), lr=1e-5)

EPOCHS = 6  # 幸運數字
jindu = 0
for epoch in range(EPOCHS):
    running_loss = 0.0
    for data in trainloader:
        tokens_tensors, segments_tensors, \
        masks_tensors, labels = [t.to(device) for t in data]
        # 將參數梯度歸零
        
        optimizer.zero_grad()
        # forward pass
        # model.eval() # 我加的，不知道幹嘛的
        outputs = model(input_ids=tokens_tensors, 
                        token_type_ids=segments_tensors, 
                        attention_mask=masks_tensors, 
                        labels=labels)
        loss = outputs[0]
        # backward
        loss.backward()
        optimizer.step()

        # 紀錄當前 batch loss
        running_loss += loss.item()
        
        jindu += BATCH_SIZE
        print (jindu)

    # 計算分類準確率
    _, acc = get_predictions(model, trainloader, compute_acc=True)

    print('[epoch %d] loss: %.3f, acc: %.3f' %
          (epoch + 1, running_loss, acc))

Fri Dec  3 17:12:42 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.91.03    Driver Version: 460.91.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  GeForce GTX 107...  Off  | 00000000:03:00.0 Off |                  N/A |
|  0%   42C    P8     7W / 180W |      2MiB /  8119MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  GeForce RTX 208...  Off  | 00000000:0A:00.0 Off |                  N/A |
|  0%   

line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


...

line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21
line 21


In [ ]:
%%time
# 建立測試集。這邊我們可以用跟訓練時不同的 batch_size(256)，看你 GPU 多大
testset = FakeNewsDataset("test", tokenizer=tokenizer)
testloader = DataLoader(testset, batch_size=256, 
                        collate_fn=create_mini_batch)

# 用分類模型預測測試集
predictions = get_predictions(model, testloader)

# 用來將預測的 label id 轉回 label 文字
index_map = {v: k for k, v in testset.label_map.items()}

# 生成 Kaggle 繳交檔案
df = pd.DataFrame({"Category": predictions.tolist()})
df['Category'] = df.Category.apply(lambda x: index_map[x])
df_pred = pd.concat([testset.df.loc[:, ["Id"]], 
                          df.loc[:, 'Category']], axis=1)
df_pred.to_csv('bert_1_prec_training_samples.csv', index=False)
df_pred.head()

In [ ]:
predictions = get_predictions(model, trainloader)
df = pd.DataFrame({"predicted": predictions.tolist()})
df['predicted'] = df.predicted.apply(lambda x: index_map[x])
df1 = pd.concat([trainset.df, df.loc[:, 'predicted']], axis=1)
like_tp = ((df1.label == 'like') & \
                (df1.label == df1.predicted) & \
                (df1.text_a.apply(lambda x: True if len(x) < 10 else False)))
df1[like_tp].head()

In [ ]:
len(predictions)

In [ ]:
n=0
for i, x in enumerate(predictions):
    print(list(x))
    n+=1
    if n>100:
        break